# 상가 점포명 모음 

# 출처: 김문과의 데이터 
https://data101.oopy.io/recommendation-engine-cosine-similarity

In [1]:
!pwd


/Users/wonny/commercial_district_analysis/kimwon/NaverMap


In [2]:
import numpy as np

In [3]:
import pandas as pd


In [25]:
df= pd.read_csv('/Users/wonny/commercial_district_analysis/crawling_data/df4.csv',index_col=0)

In [26]:
df

상호명  행정동명       행정동코드
12000         바사쿠  중계4동  1135062400
12001        산천식당  중계4동  1135062400
12002       삿갓봉초밥  중계4동  1135062400
12003  춘천최부자숯불닭갈비  중계4동  1135062400
12004        투존치킨  중계4동  1135062400
...           ...   ...         ...
14995     풍년집정육식당  구로4동  1153055000
14996      감미골뚱돼지  구로4동  1153055000
14997      핫선마늘통닭  구로4동  1153055000
14998        청년피자  구로4동  1153055000
14999        동아상회  구로4동  1153055000

[3000 rows x 3 columns]

# 크롤링

In [27]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
from selenium.common.exceptions import NoSuchElementException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import Select
import time


chromedriver = 'kimwon/chromedriver' 
driver = webdriver.Chrome(chromedriver) 


# 네이버 지도 검색창에 [~동 @@식당]으로 검색해 정확도를 높여야 합니다. 검색어를 미리 설정해줍시다.

df['naver_keyword'] = df['행정동명'] + "%20" + df['상호명']  # "%20"는 띄어쓰기를 의미합니다.
df['naver_map_url'] = ''


# 본격적으로 가게 상세페이지의 URL을 가져옵시다

for i, keyword in enumerate(df['naver_keyword'].tolist()):
    print("이번에 찾을 키워드 :", i, f"/ {df.shape[0] -1} 행", keyword)
    try:
        naver_map_search_url = f"https://m.map.naver.com/search2/search.naver?query={keyword}&sm=hty&style=v5"
        
        driver.get(naver_map_search_url)
        time.sleep(2)
        df.iloc[i,-1] = driver.find_element(By.CSS_SELECTOR,"#ct > div.search_listview._content._ctList > ul > li:nth-child(1) > div.item_info > a.a_item.a_item_distance._linkSiteview").get_attribute('data-cid')
        # 네이버 지도 시스템은 data-cid에 url 파라미터를 저장해두고 있었습니다.
        # data-cid 번호를 뽑아두었다가 기본 url 템플릿에 넣어 최종적인 url을 완성하면 됩니다.
        
        #만약 검색 결과가 없다면?
    except Exception as e1:
        if "li:nth-child(1)" in str(e1):  # -> "child(1)이 없던데요?"
            try:
                df.iloc[i,-1] = driver.find_element(By.CSS_SELECTOR, "#ct > div.search_listview._content._ctList > ul > li:nth-child(1) > div.item_info > a.a_item.a_item_distance._linkSiteview").get_attribute('data-cid')
                time.sleep(1)
            except Exception as e2:
                print(e2)
                df.iloc[i,-1] = np.nan
                time.sleep(1)
        else:
            pass


driver.quit()


# 이때 수집한 것은 완전한 URL이 아니라 URL에 들어갈 ID (data-cid 라는 코드명으로 저장된) 이므로, 온전한 URL로 만들어줍니다

df['naver_map_url'] = "https://m.place.naver.com/restaurant/" + df['naver_map_url']


# URL이 수집되지 않은 데이터는 제거합니다.
df = df.loc[~df['naver_map_url'].isnull()]

/var/folders/s3/xdg3f00d5gz2dnfsw7wsjyjc0000gn/T/ipykernel_33488/912338001.py:13: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(chromedriver)


이번에 찾을 키워드 : 0 / 2999 행 중계4동%20바사쿠
Message: no such element: Unable to locate element: {"method":"css selector","selector":"#ct > div.search_listview._content._ctList > ul > li:nth-child(1) > div.item_info > a.a_item.a_item_distance._linkSiteview"}
  (Session info: chrome=110.0.5481.100)
Stacktrace:
0   chromedriver                        0x0000000103002138 chromedriver + 4923704
1   chromedriver                        0x0000000102f7a9d3 chromedriver + 4368851
2   chromedriver                        0x0000000102bc3787 chromedriver + 472967
3   chromedriver                        0x0000000102c07ba3 chromedriver + 752547
4   chromedriver                        0x0000000102c07df1 chromedriver + 753137
5   chromedriver                        0x0000000102c4e734 chromedriver + 1042228
6   chromedriver                        0x0000000102c30fdd chromedriver + 921565
7   chromedriver                        0x0000000102c4bc0f chromedriver + 1031183
8   chromedriver                        0x00000

In [28]:
df.to_csv('/Users/wonny/commercial_district_analysis/crawling_data/df4_phase1.csv', index=False)

In [30]:
df= pd.read_csv('/Users/wonny/commercial_district_analysis/crawling_data/df4_phase1.csv')
df

상호명  행정동명       행정동코드     naver_keyword  \
0        삿갓봉초밥  중계4동  1135062400      중계4동%20삿갓봉초밥   
1         투존치킨  중계4동  1135062400       중계4동%20투존치킨   
2    싹쓰리솥뚜껑삼겹살  중계4동  1135062400  중계4동%20싹쓰리솥뚜껑삼겹살   
3         서원갈비  중계4동  1135062400       중계4동%20서원갈비   
4         메가커피  중계4동  1135062400       중계4동%20메가커피   
..         ...   ...         ...               ...   
802       라프리앙  구의3동  1121587000       구의3동%20라프리앙   
803       집파스타  구의3동  1121587000       구의3동%20집파스타   
804     투썸플레이스  구의3동  1121587000     구의3동%20투썸플레이스   
805       홍과자점  구의3동  1121587000       구의3동%20홍과자점   
806       청년피자  구로4동  1153055000       구로4동%20청년피자   

                                       naver_map_url  
0    https://m.place.naver.com/restaurant/1634299593  
1    https://m.place.naver.com/restaurant/1119548075  
2     https://m.place.naver.com/restaurant/602057598  
3      https://m.place.naver.com/restaurant/37554064  
4    https://m.place.naver.com/restaurant/1815979563  
..                                               ...  
802  https://m.place.naver.com/restaurant/1163290291  
803    https://m.place.naver.com/restaurant/37683843  
804    https://m.place.naver.com/restaurant/36948822  
805  https://m.place.naver.com/restaurant/1988869021  
806  https://m.place.naver.com/restaurant/1201019799  

[807 rows x 5 columns]

In [15]:
# 각 데이터들을 미리 리스트에 담은 다음, 마지막에 데이터 프레임에 합칠 것입니다.


chromedriver = 'chromedriver' 


vistor_review_qty_list = []
blog_review_qty_list = []
star_review_stars_list = []


driver = webdriver.Chrome(chromedriver) 


for i, url in enumerate(df['naver_map_url']):

    driver.get(url)
    time.sleep(2)
    # 네이버 지도의 유형 분류

    try:


        # 네이버 지도의 유형 분류
        vistor_review_qty = driver.find_element(By.XPATH, '//*[@id="app-root"]/div/div/div/div[2]/div[1]/div[2]/span[2]/a/em').text

        # 블로그 리뷰 수
        blog_review_qty = driver.find_element(By.XPATH, '//*[@id="app-root"]/div/div/div/div[2]/div[1]/div[2]/span[3]/a/em').text
        # 블로그 별점 점수
        star_review_stars = driver.find_element(By.XPATH,'//*[@id="app-root"]/div/div/div/div[2]/div[1]/div[2]/span[1]/em').text

        vistor_review_qty_list.append(vistor_review_qty)
        blog_review_qty_list.append(blog_review_qty)
        star_review_stars_list.append(star_review_stars)

    # 리뷰가 없는 업체는 크롤링에 오류가 뜨므로 표기해둡니다.
    except Exception as e1:
        print(f"{i}행 문제가 발생")
        
        # 리뷰가 없으므로 null을 임시로 넣어줍니다.
        vistor_review_qty_list.append('null')
        blog_review_qty_list.append('null')
        star_review_stars_list.append('null')


        
driver.quit()

df['naver_visitor_review_qty'] = vistor_review_qty_list  # 네이버 상세페이지에서 크롤링한 업체 유형
df['naver_star_point'] = star_review_stars_list  # 네이버 상세페이지에서 평가한 별점 평점
df['naver_blog_review_qty'] = blog_review_qty_list  # 네이버 상세페이지에 나온 블로그 리뷰의 총 개수

7행 문제가 발생
8행 문제가 발생
10행 문제가 발생
14행 문제가 발생
28행 문제가 발생
29행 문제가 발생
33행 문제가 발생
35행 문제가 발생
40행 문제가 발생
41행 문제가 발생
42행 문제가 발생
48행 문제가 발생
49행 문제가 발생
52행 문제가 발생
55행 문제가 발생
57행 문제가 발생
64행 문제가 발생
70행 문제가 발생
71행 문제가 발생
75행 문제가 발생
77행 문제가 발생
82행 문제가 발생
87행 문제가 발생
90행 문제가 발생
96행 문제가 발생
100행 문제가 발생
101행 문제가 발생
115행 문제가 발생
125행 문제가 발생
127행 문제가 발생
128행 문제가 발생
130행 문제가 발생
133행 문제가 발생
142행 문제가 발생
147행 문제가 발생
154행 문제가 발생
155행 문제가 발생
157행 문제가 발생
158행 문제가 발생
159행 문제가 발생
162행 문제가 발생
166행 문제가 발생
170행 문제가 발생
180행 문제가 발생
193행 문제가 발생
195행 문제가 발생
196행 문제가 발생
208행 문제가 발생
210행 문제가 발생
218행 문제가 발생
220행 문제가 발생
225행 문제가 발생
227행 문제가 발생
231행 문제가 발생
232행 문제가 발생
237행 문제가 발생
239행 문제가 발생
240행 문제가 발생
253행 문제가 발생
255행 문제가 발생
257행 문제가 발생
265행 문제가 발생
267행 문제가 발생
274행 문제가 발생
286행 문제가 발생
288행 문제가 발생
292행 문제가 발생
293행 문제가 발생
300행 문제가 발생
303행 문제가 발생
305행 문제가 발생
308행 문제가 발생
310행 문제가 발생
312행 문제가 발생
318행 문제가 발생
321행 문제가 발생
324행 문제가 발생
325행 문제가 발생
328행 문제가 발생
338행 문제가 발생
340행 문제가 발생
344행 문제가 발생
348행 문제가 발생
349행 문제가 발생
351행 문제가 발생
355행 문제

In [29]:
df

상호명  행정동명       행정동코드     naver_keyword  \
12002      삿갓봉초밥  중계4동  1135062400      중계4동%20삿갓봉초밥   
12004       투존치킨  중계4동  1135062400       중계4동%20투존치킨   
12005  싹쓰리솥뚜껑삼겹살  중계4동  1135062400  중계4동%20싹쓰리솥뚜껑삼겹살   
12006       서원갈비  중계4동  1135062400       중계4동%20서원갈비   
12007       메가커피  중계4동  1135062400       중계4동%20메가커피   
...          ...   ...         ...               ...   
14868       라프리앙  구의3동  1121587000       구의3동%20라프리앙   
14869       집파스타  구의3동  1121587000       구의3동%20집파스타   
14871     투썸플레이스  구의3동  1121587000     구의3동%20투썸플레이스   
14873       홍과자점  구의3동  1121587000       구의3동%20홍과자점   
14998       청년피자  구로4동  1153055000       구로4동%20청년피자   

                                         naver_map_url  
12002  https://m.place.naver.com/restaurant/1634299593  
12004  https://m.place.naver.com/restaurant/1119548075  
12005   https://m.place.naver.com/restaurant/602057598  
12006    https://m.place.naver.com/restaurant/37554064  
12007  https://m.place.naver.com/restaurant/1815979563  
...                                                ...  
14868  https://m.place.naver.com/restaurant/1163290291  
14869    https://m.place.naver.com/restaurant/37683843  
14871    https://m.place.naver.com/restaurant/36948822  
14873  https://m.place.naver.com/restaurant/1988869021  
14998  https://m.place.naver.com/restaurant/1201019799  

[807 rows x 5 columns]

# 여기까지하고 저장하쇼!!! 

In [16]:
df.to_csv('/Users/wonny/commercial_district_analysis/crawling_data/df3_final.csv',index=False)